In [29]:
import math
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import shutil
import sys

#date = input("Enter User Name or Date:")
#whichList = input("First Sim (1), Second (2), or Third (3), (4)?")

date = 'User3'
word = 'posPhal'
addword = ''
projectionData = None

list_beta = [1.05]
list_gamma = [0]


def progress(count, total, suffix=''):
    bar_len = 60
    filled_len = int(round(bar_len * count / float(total)))

    percents = round(100.0 * count / float(total), 1)
    bar = '=' * filled_len + '-' * (bar_len - filled_len)

    sys.stdout.write('[%s] %s%s ...%s\r' % (bar, percents, '%', suffix))
    sys.stdout.flush()  # As suggested by Rom Ruben

# projectionData = pd.read_csv('./Analysis/WriteHere//'+ date + '/G-' + str(gamma) + '-B-' + str(beta) + '-' + word + date + '.csv', sep = ";", decimal = '.')#, low_memory = False)
read = 0
for read in range(0, len(list_beta)):
    gamma = list_gamma[read]
    beta = list_beta[read]
    print(gamma, beta)
    projectionData = pd.read_csv('../Assets/Resources/DataSimulation/AlgoHints/NoParam-G-' + str(gamma) + '-B-' + str(beta) + '-' + word + date + '.csv', sep = ";", decimal = '.')#, low_memory = False)

    projectionData = projectionData.dropna()

    projectionData['BoneName.0'] = projectionData['BoneName']
    projectionData['BoneNameL.0'] = projectionData['BoneNameL']

    projectionData['BonePos.0'] = projectionData['BonePos']
    projectionData['BonePosL.0'] = projectionData['BonePosL']

    projectionData['PosPred.0'] = projectionData['PosPred']
    
    projectionData['PosPredL.0'] = projectionData['PosPredL']
    
    projectionData['DistToPred.0'] = projectionData['DistToPred']
    
    projectionData['DistToPredL.0'] = projectionData['DistToPredL']
    
    projectionData['BoneRadius.0'] = projectionData['BoneRadius']
    projectionData['BoneContact.0'] = projectionData['BoneContact']

    projectionData['BoneRadiusL.0'] = projectionData['BoneRadiusL']
    projectionData['BoneContactL.0'] = projectionData['BoneContactL']

    projectionData['ClosestPoint.0'] = projectionData['ClosestPoint']
    projectionData['ClosestPointL.0'] = projectionData['ClosestPointL']

    projectionData['DistToClosest.0'] = projectionData['DistToClosest']
    projectionData['DistToClosestL.0'] = projectionData['DistToClosestL']

    for i in range(0, 135):
        cond1 = projectionData['Config'] == i
        projectionData = projectionData.drop(projectionData[projectionData['Config'] == i].index[0:2])

    for j in range(0,19):
        projectionData.loc[projectionData['BoneContact.'+str(j)] == True, 'Touching.'+str(j)] = projectionData['BonePos.'+str(j)]
        projectionData.loc[projectionData['BoneContactL.'+str(j)] == True, 'TouchingL.'+str(j)] = projectionData['BonePosL.'+str(j)]
        
    predictionsData = None
    predictionsData = pd.DataFrame(columns = ['Beta', 'Gamma'])


    for i in range(0,135):
        indexContact = 0
        indexPrediction = 0
        indexPrediction1 = 0
        indexPrediction2 = 0

        indexStart = []

        indexCond = 0
        
        indexContactL = 0
        indexPredictionL = 0
        indexPrediction1L = 0
        indexPrediction2L = 0

        progress(i, 135)

        if(len(projectionData[projectionData['Config'] == i]) != 0):
            cond1 = (projectionData['Config'] == i)
            predictionsData.loc[i] = pd.Series({'Gamma' : projectionData[cond1]['Gamma'].iloc[0], 'Beta' : projectionData[cond1]['Beta'].iloc[0]})

            for j in range(0, 19):                                                
                
                predictionsData.loc[i, 'Contact.'+str(j)] = len(projectionData[cond1]['Touching.'+str(j)].dropna()) != 0
                predictionsData.loc[i, 'ContactL.'+str(j)] = len(projectionData[cond1]['TouchingL.'+str(j)].dropna()) != 0

                if(len(projectionData[cond1]['Touching.'+str(j)].dropna()) != 0):
                    indexContact = projectionData[cond1]['Touching.'+str(j)].dropna().index[0]
                    print(j, projectionData[cond1]['Touching.'+str(j)].dropna().index[0])

                    if(np.isnan(projectionData['Touching.'+str(j)][indexContact]) == False):
                        print(j, abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['PosPred.'+str(j)][indexContact]))
                        indexCond = projectionData[cond1]['Time'].index
                        
                        nameBoneDist = 'DistBoneInTolTime0.'+str(j)+'.0'
                        predictionsData.loc[i, nameBoneDist] = 1000*(abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['BonePos.'+str(j)][indexContact]))

                        #print(i, j, predictionsData[nameBoneDist].iloc[i], projectionData['DistToPred.'+str(j)][indexContact], abs(predictionsData[nameBoneDist].iloc[i] - 1000*projectionData['DistToPred.'+str(j)][indexContact]))

                        nameDist = 'MaxDistanceInTolTime0.'+str(j)+'.0'
                        predictionsData.loc[i, nameDist] = 1000*(abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['PosPred.'+str(j)][indexContact]) - projectionData['BoneRadius.'+str(j)][indexContact])

                        nameDistPred = 'DistToPred.'+str(j)+'.0'
                        predictionsData.loc[i, nameDistPred] = 1000*projectionData['DistToPred.'+str(j)][indexContact]

                        for k in range(300, 2050, 50):
                            tolerance = k/1000
                            indexStart = []
                            indexPrediction = 0
                            indexPrediction1 = 0
                            indexPrediction2 = 0
                            indexTamere = 0

                            for p in range(0, len(indexCond)):
                                if((projectionData['Time'][indexContact] - projectionData['Time'][indexCond[p]]) > 0):
                                    if(projectionData['Time'][indexContact] - projectionData['Time'][indexCond[p]] <= tolerance):
                                        if((projectionData['Time'][indexContact] - projectionData['Time'][indexCond[p]]) >= tolerance - 0.05):

                                            indexStart.append(indexCond[p])
                            
                            indexTamere = indexStart
                            if(len(indexTamere) != 0):
                                indexPrediction = indexTamere[0]
                                for q in range(1, len(indexTamere)):
                                    if( abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['PosPred.'+str(j)][indexPrediction] ) < abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['PosPred.'+str(j)][indexTamere[q]]) ):
                                        indexPrediction = indexTamere[q]
                                    else:
                                        pass
                                nameDist = 'MaxDistanceInTolTime0.'+str(j)+'.'+str(k)
                                nameClos = 'DistToClos0.'+str(j)+'.'+str(k)
                                nameBoneDist = 'DistBoneInTolTime0.'+str(j)+'.'+str(k)

                                predictionsData.loc[i, nameDist] = 1000*(abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['PosPred.'+str(j)][indexPrediction]) - projectionData['BoneRadius.'+str(j)][indexPrediction])
                                predictionsData.loc[i, nameClos] = 1000*(abs(projectionData['ClosestPoint.'+str(j)][indexPrediction] - projectionData['PosPred.'+str(j)][indexPrediction]) - projectionData['BoneRadius.'+str(j)][indexPrediction])
                                predictionsData.loc[i, nameBoneDist] = 1000*(abs(projectionData['Touching.'+str(j)][indexContact] - projectionData['BonePos.'+str(j)][indexPrediction]))

                                nameDistPred = 'DistToPred.'+str(j)+'.'+str(k)

                                predictionsData.loc[i, nameDistPred] = 1000*projectionData['DistToPred.'+str(j)][indexPrediction]
                                
                                print(k, j, indexPrediction, abs(projectionData['PosPred.'+str(j)][indexPrediction]- projectionData['BonePos.'+str(j)][indexContact]), 1000*projectionData['DistToPred.'+str(j)][indexPrediction])
                            else:
                                pass
                    else:
                        pass
                else:
                    pass

                if(len(projectionData[cond1]['TouchingL.'+str(j)].dropna()) != 0):
                    indexContactL = projectionData[cond1]['TouchingL.'+str(j)].dropna().index[0]

                    if(np.isnan(projectionData['TouchingL.'+str(j)][indexContactL]) == False):
                        
                        indexCond = projectionData[cond1]['Time'].index

                        nameBoneDist = 'DistBoneInTolTimeL0.'+str(j)+'.0'
                        predictionsData.loc[i, nameBoneDist] = 1000*(abs(projectionData['TouchingL.'+str(j)][indexContactL] - projectionData['BonePosL.'+str(j)][indexContactL]))

                        nameDist = 'MaxDistanceInTolTimeL0.'+str(j)+'.0'
                        predictionsData.loc[i, nameDist] = 1000*(abs(projectionData['TouchingL.'+str(j)][indexContactL] - projectionData['PosPredL.'+str(j)][indexContactL]) - projectionData['BoneRadius.'+str(j)][indexContactL])
                        
                        nameDistPred = 'DistToPredL.'+str(j)+'.0'
                        predictionsData.loc[i, nameDistPred] = 1000*projectionData['DistToPredL.'+str(j)][indexContactL]
                        
                        for k in range(300, 2050, 50):
                            tolerance = k/1000

                            indexStart = []
                            indexPredictionL = 0
                            indexPrediction1L = 0
                            indexPrediction2L = 0
                            indexTamere = 0
                        
                            for p in range(0, len(indexCond)):
                                if((projectionData['Time'][indexContactL] - projectionData['Time'][indexCond[p]]) > 0):
                                    if(projectionData['Time'][indexContactL] - projectionData['Time'][indexCond[p]] <= tolerance):
                                        if((projectionData['Time'][indexContactL] - projectionData['Time'][indexCond[p]]) >= tolerance - 0.05):

                                            indexStart.append(indexCond[p])
                            
                            indexTamere = indexStart
                            if(len(indexTamere) != 0):    
                                indexPredictionL = indexTamere[0]
                                for q in range(1, len(indexTamere)):
                                    if( abs(projectionData['TouchingL.'+str(j)][indexContactL] - projectionData['PosPredL.'+str(j)][indexPredictionL] ) < abs(projectionData['TouchingL.'+str(j)][indexContactL] - projectionData['PosPredL.'+str(j)][indexTamere[q]]) ):
                                        indexPredictionL = indexTamere[q]
                                    else:
                                        pass

                                nameDist = 'MaxDistanceInTolTimeL0.'+str(j)+'.'+str(k)
                                nameClos = 'DistToClosL0.'+str(j)+'.'+str(k)
                                nameBoneDist = 'DistBoneInTolTimeL0.'+str(j)+'.'+str(k)

                                predictionsData.loc[i, nameBoneDist] = 1000*(abs(projectionData['TouchingL.'+str(j)][indexContactL] - projectionData['BonePosL.'+str(j)][indexPredictionL]))
                                predictionsData.loc[i, nameDist] = 1000*(abs(projectionData['TouchingL.'+str(j)][indexContactL] - projectionData['PosPredL.'+str(j)][indexPredictionL]) - projectionData['BoneRadiusL.'+str(j)][indexPredictionL])
                                predictionsData.loc[i, nameClos] = 1000*(abs(projectionData['ClosestPointL.'+str(j)][indexPredictionL] - projectionData['PosPredL.'+str(j)][indexPredictionL]) - projectionData['BoneRadiusL.'+str(j)][indexPredictionL])

                                nameDistPred = 'DistToPredL.'+str(j)+'.'+str(k)
                                predictionsData.loc[i, nameDistPred] = 1000*projectionData['DistToPredL.'+str(j)][indexPredictionL]
                                
                            else:
                                pass  
                    else:
                        pass
                else:
                    pass


0 1.05
6 12568------------------------------------------------------] 2.2% ...
6 0.009197600000000139
300 6 12563 0.014510899999999993 26.412599999999998
350 6 12562 0.013360499999999997 30.64463
400 6 12561 0.008776800000000029 30.53848
450 6 12560 0.0024226000000001635 31.622579999999996
500 6 12559 0.0005839999999999179 36.7168
550 6 12558 0.001982199999999934 47.15238
600 6 12557 0.0020460999999999396 60.714999999999996
650 6 12556 0.0017495000000000704 74.14661
700 6 12555 0.00043599999999999195 89.25726
750 6 12554 0.0039877000000001495 100.8967
800 6 12553 0.011724600000000085 108.73510000000002
850 6 12552 0.022177500000000072 115.6492
900 6 12551 0.034378300000000084 133.9015
950 6 12550 0.05158230000000008 150.6476
1000 6 12549 0.05241629999999997 172.0541
1050 6 12548 0.05241629999999997 182.09270000000004
1100 6 12546 0.07198570000000004 262.645
1150 6 12545 0.07198570000000004 316.5407
1200 6 12544 0.07198570000000004 356.8048
1250 6 12543 0.07198570000000004 399.565
1350 

In [98]:
predictionsData.loc[3]

Beta                                  1.05
Gamma                                    0
Contact.0                            False
ContactL.0                            True
DistBoneInTolTimeL0.0.0                  0
MaxDistanceInTolTimeL0.0.0         536.165
DistToPredL.0.0                    554.393
DistBoneInTolTimeL0.0.300          71.3916
MaxDistanceInTolTimeL0.0.300       10.3933
DistToClosL0.0.300                -11.9461
DistToPredL.0.300                  52.6211
DistBoneInTolTimeL0.0.350          71.8124
MaxDistanceInTolTimeL0.0.350       12.1847
DistToClosL0.0.350                -13.6649
DistToPredL.0.350                  52.2481
DistBoneInTolTimeL0.0.400          71.5983
MaxDistanceInTolTimeL0.0.400        12.023
DistToClosL0.0.400                -13.6332
DistToPredL.0.400                  51.7709
DistBoneInTolTimeL0.0.450          71.5479
MaxDistanceInTolTimeL0.0.450       11.3718
DistToClosL0.0.450                -13.4826
DistToPredL.0.450                  52.6107
DistBoneInT

In [99]:
read = 0
for read in range(0, len(list_beta)):
    gamma = list_gamma[read]
    beta = list_beta[read]
    print(gamma, beta)
    analysisA = None
    analysisA = pd.read_csv('./Analysis/WriteHere/NoParam-G-' + str(gamma) + 'B-' + str(beta) + addword +'-'+ date + '-FullAnalysis-' + word + '.csv', sep = ";", decimal = '.', low_memory = False)

    boneNames = []
    bones = pd.Series()
    bones = pd.read_csv('./BoneNames.csv')
    bones = bones.transpose()
    bones = bones.drop(bones.index[0])
    for i in range(0, 19):
        boneNames.append('R-' + bones.iloc[0, i])
    for i in range(0, 19):
        boneNames.append('L-' + bones.iloc[0, i])
        

    analyseMe = pd.DataFrame(columns = ['Config'])
    def progress(count, total, suffix=''):
        bar_len = 60
        filled_len = int(round(bar_len * count / float(total)))

        percents = round(100.0 * count / float(total), 1)
        bar = '=' * filled_len + '-' * (bar_len - filled_len)

        sys.stdout.write('[%s] %s%s ...%s\r' % (bar, percents, '%', suffix))
        sys.stdout.flush()  # As suggested by Rom Ruben

    progress(0, 135)    
    for i in range(0, 135):
        analyseMe.loc[i] = pd.Series({'Config' : i})
        for j in range(0, 19):
            analyseMe['Contact.'+str(j)] = analysisA['Contact.'+str(j)]
            analyseMe['Contact.'+str(j+19)] = analysisA['ContactL.'+str(j)]
            
            k = 0
            name = 'MaxDistanceInTolTime0.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)] = 0
                
            name = 'MaxDistanceInTolTimeL0.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['MaxDistanceInTolTime.'+str(j+19)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['MaxDistanceInTolTime.'+str(j+19)+'.'+str(k)] = 0

            name = 'DistToPred.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['DistToPred.'+str(j)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['DistToPred.'+str(j)+'.'+str(k)] = 0

            name = 'DistToPredL.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['DistToPred.'+str(j+19)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['DistToPred.'+str(j+19)+'.'+str(k)] = 0
                
            name = 'MaxDistanceInTolTimeL0.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['MaxDistanceInTolTime.'+str(j+19)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['MaxDistanceInTolTime.'+str(j+19)+'.'+str(k)] = 0

            name = 'DistBoneInTolTime0.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['DistBoneInTolTime.'+str(j)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['DistBoneInTolTime.'+str(j)+'.'+str(k)] = 0
                
            name = 'DistBoneInTolTimeL0.'+str(j)+'.'+str(k)
            if(name in analysisA.columns):
                analyseMe['DistBoneInTolTime.'+str(j+19)+'.'+str(k)] = analysisA[name]
            else:
                analyseMe['DistBoneInTolTime.'+str(j+19)+'.'+str(k)] = 0

            for k in range(300, 2050, 50):
                name = 'MaxDistanceInTolTime0.'+str(j)+'.'+str(k)
                if(name in analysisA.columns):
                    analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)] = analysisA[name]
                else:
                    analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)] = 0
                    
                name = 'MaxDistanceInTolTimeL0.'+str(j)+'.'+str(k)
                if(name in analysisA.columns):
                    analyseMe['MaxDistanceInTolTime.'+str(j+19)+'.'+str(k)] = analysisA[name]
                else:
                    analyseMe['MaxDistanceInTolTime.'+str(j+19)+'.'+str(k)] = 0

                name = 'DistBoneInTolTime0.'+str(j)+'.'+str(k)
                if(name in analysisA.columns):
                    analyseMe['DistBoneInTolTime.'+str(j)+'.'+str(k)] = analysisA[name]
                else:
                    analyseMe['DistBoneInTolTime.'+str(j)+'.'+str(k)] = 0
                    
                name = 'DistBoneInTolTimeL0.'+str(j)+'.'+str(k)
                if(name in analysisA.columns):
                    analyseMe['DistBoneInTolTime.'+str(j+19)+'.'+str(k)] = analysisA[name]
                else:
                    analyseMe['DistBoneInTolTime.'+str(j+19)+'.'+str(k)] = 0

                name = 'DistToPred.'+str(j)+'.'+str(k)
                if(name in analysisA.columns):
                    analyseMe['DistToPred.'+str(j)+'.'+str(k)] = analysisA[name]
                else:
                    analyseMe['DistToPred.'+str(j)+'.'+str(k)] = 0

                name = 'DistToPredL.'+str(j)+'.'+str(k)
                if(name in analysisA.columns):
                    analyseMe['DistToPred.'+str(j+19)+'.'+str(k)] = analysisA[name]
                else:
                    analyseMe['DistToPred.'+str(j+19)+'.'+str(k)] = 0



0 1.05


In [151]:
meanDistInTol = pd.DataFrame()

for i in range(0, 135):
    progress(i, 4*135)
    for j in range(0, 38):
        k = 0
        if((analyseMe['Contact.'+str(j)].loc[i] == 'True') | (analyseMe['Contact.'+str(j)].loc[i] == '1.0')):
            nameBoneDist = 'DistBoneInTolTime.'+str(j)+'.'+str(k)
            meanDistInTol.loc[i, nameBoneDist] = analyseMe[nameBoneDist].loc[i]
            nameBonePred = 'DistToPred.'+str(j)+'.'+str(k)
            meanDistInTol.loc[i, nameBonePred] = analyseMe[nameBonePred].loc[i]
            name = 'DistanceInTolTime.'+str(j)+'.'+str(k)
            if(analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)].loc[i] > 0):
                meanDistInTol.loc[i, name] = analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)].loc[i]
            else:
                meanDistInTol.loc[i, name] = 0     

        else:
            pass
        
        for k in range(300, 2050, 50):
            if((analyseMe['Contact.'+str(j)].loc[i] == 'True') | (analyseMe['Contact.'+str(j)].loc[i] == '1.0')):
                nameBoneDist = 'DistBoneInTolTime.'+str(j)+'.'+str(k)
                meanDistInTol.loc[i, nameBoneDist] = analyseMe[nameBoneDist].loc[i]
                nameBonePred = 'DistToPred.'+str(j)+'.'+str(k)
                meanDistInTol.loc[i, nameBonePred] = analyseMe[nameBonePred].loc[i]
                
                name = 'DistanceInTolTime.'+str(j)+'.'+str(k)
                if(analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)].loc[i] > 0):
                    meanDistInTol.loc[i, name] = analyseMe['MaxDistanceInTolTime.'+str(j)+'.'+str(k)].loc[i]
                else:
                    meanDistInTol.loc[i, name] = 0         
                
            else:
                pass

meanDistPerTol = pd.DataFrame()
meanDistHand = pd.DataFrame()

nbPlanes = 0
meanDistPhal = 0
meanDistAllPhal = 0
nbPhal = 0
meanDistMorePhal = 0

for i in range(0, 135):
    progress(i + 135, 4*135)

    k = 0
    name = 'DistanceInTolTime.'+str(k)
    nameBoneDist = 'DistBoneInTolTime.'+str(k)
    nameBonePred = 'DistToPred.'+str(k)
    nbPhalDist = 0
    nbBone = 0
    nbPred = 0    
    meanDistPhal = 0
    meanBoneDistPhal = 0
    meanDistPred = 0
    for j in range(0, 38):
        if((analyseMe['Contact.'+str(j)].loc[i] == 'True') | (analyseMe['Contact.'+str(j)].loc[i] == '1.0')):
            if(np.isnan(meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].loc[i]) == False):
                meanDistPhal = meanDistPhal + meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].loc[i]
                nbPhalDist = nbPhalDist + 1
            else:
                pass
            if(np.isnan(meanDistInTol['DistBoneInTolTime.'+str(j)+'.'+str(k)].loc[i]) == False):
                meanBoneDistPhal = meanBoneDistPhal + meanDistInTol['DistBoneInTolTime.'+str(j)+'.'+str(k)].loc[i]
                nbBone = nbBone + 1
            else:
                pass
            if(np.isnan(meanDistInTol['DistToPred.'+str(j)+'.'+str(k)].loc[i]) == False):
                meanDistPred = meanDistPred + meanDistInTol['DistToPred.'+str(j)+'.'+str(k)].loc[i]
                nbPred = nbPred + 1
            else:
                pass

            if(len(meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].dropna()) != 0):
                meanDistPerTol.loc[k, 'Phalanx.'+str(j)] = meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].dropna().mean()   
                meanDistPerTol.loc[k, 'BoneDist.'+str(j)] = meanDistInTol['DistBoneInTolTime.'+str(j)+'.'+str(k)].dropna().mean()
                meanDistPerTol.loc[k, 'DistToPred.'+str(j)] = meanDistInTol['DistToPred.'+str(j)+'.'+str(k)].dropna().mean()
            else:
                pass
        else:
            pass

    if(nbPhalDist != 0):
        meanDistHand.loc[i, name] = meanDistPhal/nbPhalDist
    else:
        pass
    if(nbBone != 0):
        meanDistHand.loc[i, nameBoneDist] = meanBoneDistPhal/nbBone
    else:
        pass
    if(nbPred != 0):
        meanDistHand.loc[i, nameBonePred] = meanDistPred/nbPred
    else:
        pass
    
    for k in range(300, 2050, 50):
        name = 'DistanceInTolTime.'+str(k)
        nameBoneDist = 'DistBoneInTolTime.'+str(k)
        nameBonePred = 'DistToPred.'+str(k)
        nbPhalDist = 0
        nbBone = 0
        nbPred = 0
        meanDistPhal = 0
        meanBoneDistPhal = 0
        meanDistPred = 0
        for j in range(0, 38):
            if((analyseMe['Contact.'+str(j)].loc[i] == 'True') | (analyseMe['Contact.'+str(j)].loc[i] == '1.0')):
                if(np.isnan(meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].loc[i]) == False):
                    meanDistPhal = meanDistPhal + meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].loc[i]
                    nbPhalDist = nbPhalDist + 1
                else:
                    pass
                if(np.isnan(meanDistInTol['DistBoneInTolTime.'+str(j)+'.'+str(k)].loc[i]) == False):
                    meanBoneDistPhal = meanBoneDistPhal + meanDistInTol['DistBoneInTolTime.'+str(j)+'.'+str(k)].loc[i]
                    nbBone = nbBone + 1
                else:
                    pass
                if(np.isnan(meanDistInTol['DistToPred.'+str(j)+'.'+str(k)].loc[i]) == False):
                    meanDistPred = meanDistPred + meanDistInTol['DistToPred.'+str(j)+'.'+str(k)].loc[i]
                    nbPred = nbPred + 1
                else:
                    pass

                if(len(meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].dropna()) != 0):
                    meanDistPerTol.loc[k, 'Phalanx.'+str(j)] = meanDistInTol['DistanceInTolTime.'+str(j)+'.'+str(k)].dropna().mean()   
                    meanDistPerTol.loc[k, 'BoneDist.'+str(j)] = meanDistInTol['DistBoneInTolTime.'+str(j)+'.'+str(k)].dropna().mean()
                    meanDistPerTol.loc[k, 'DistToPred.'+str(j)] = meanDistInTol['DistToPred.'+str(j)+'.'+str(k)].dropna().mean()
                else:
                    pass
            else:
                pass

        if(nbPhalDist != 0):
            meanDistHand.loc[i, name] = meanDistPhal/nbPhalDist
        else:
            pass
        if(nbBone != 0):
            meanDistHand.loc[i, nameBoneDist] = meanBoneDistPhal/nbBone
        else:
            pass
        if(nbPred != 0):
            meanDistHand.loc[i, nameBonePred] = meanDistPred/nbPred
        else:
            pass

meanDistHand

DistanceInTolTime.0  DistBoneInTolTime.0  DistToPred.0  \
3             2.423606                  0.0     16.464229   

   DistanceInTolTime.300  DistBoneInTolTime.300  DistToPred.300  \
3               3.955071              25.329418       48.872735   

   DistanceInTolTime.350  DistBoneInTolTime.350  DistToPred.350  \
3              11.871153              26.390567       57.374145   

   DistanceInTolTime.400  ...  DistanceInTolTime.1850  DistBoneInTolTime.1850  \
3              10.416987  ...                5.040258                142.1645   

   DistToPred.1850  DistanceInTolTime.1900  DistanceInTolTime.1950  \
3         410.2557                     0.0                5.057283   

   DistBoneInTolTime.1950  DistToPred.1950  DistanceInTolTime.2000  \
3                142.3571         410.8747                5.142933   

   DistBoneInTolTime.2000  DistToPred.2000  
3                142.3377         410.1602  

[1 rows x 106 columns]

In [140]:
meanDistInTol['DistBoneInTolTime.'+str(9)+'.'+str(300)]

3    39.7124
Name: DistBoneInTolTime.9.300, dtype: float64

In [152]:
meanDistPerTol.sort_index(ascending = True).sort_index(axis = 1)

BoneDist.12  BoneDist.15  BoneDist.18  BoneDist.25  BoneDist.27  \
0          0.0000       0.0000       0.0000       0.0000       0.0000   
300       38.2389      24.8589      23.4153      77.2742          NaN   
350       42.8699      28.7089      27.6932      77.3528      51.4768   
400       47.5949      32.8805          NaN      67.8644      62.4146   
450       52.6924      49.7279      30.9008      77.0565      72.5424   
500       57.2329      43.5271      31.4377      71.1139      80.9073   
550       74.6732      26.1431      34.0018      57.2692      88.4277   
600       72.4078      15.9034      35.9235      50.8678          NaN   
650       56.7953      44.0451      36.7002      48.8260      93.5312   
700       45.3465      78.0728      51.3516      45.5494      95.9957   
750        6.8103     121.4115      46.2210      44.1989      96.3901   
800       23.2896     174.7398      31.8367          NaN      98.3903   
850       60.2284     185.4211      22.7498      41.1964     102.0771   
900      109.7921          NaN      29.1071      34.4173      88.0425   
950      164.2388     186.8910      58.7378      33.9343      84.7229   
1000     177.5946     193.8122     102.3196      33.8682      84.7539   
1050     183.0008     195.8034     154.7619      34.7479      89.9084   
1100     190.3643     180.6311     157.8393          NaN      96.2130   
1150          NaN     167.2059     157.0803      40.9856     105.9417   
1200     190.8412     166.3819          NaN      62.8240     115.7977   
1250     172.6173     154.7800     163.9490      85.8134     137.7372   
1300     156.2110          NaN     166.0366     123.7554     166.1372   
1350     151.9585     170.6506     154.4020     123.3439     170.4423   
1400     139.2099          NaN     145.4716          NaN     166.2946   
1450     154.5876          NaN     147.5253          NaN     183.3690   
1500          NaN          NaN     135.4281          NaN     183.1302   
1550          NaN          NaN          NaN          NaN     171.2062   
1600          NaN          NaN     149.7731          NaN     158.1199   
1650          NaN          NaN          NaN          NaN     149.9643   
1700          NaN          NaN          NaN          NaN     148.2201   
1750          NaN          NaN          NaN          NaN     148.0154   
1800          NaN          NaN          NaN          NaN     147.6798   
1850          NaN          NaN          NaN          NaN     142.1645   
1900          NaN          NaN          NaN          NaN          NaN   
1950          NaN          NaN          NaN          NaN     142.3571   
2000          NaN          NaN          NaN          NaN     142.3377   

      BoneDist.28  BoneDist.30  BoneDist.31  BoneDist.34  BoneDist.37  ...  \
0          0.0000       0.0000       0.0000       0.0000       0.0000  ...   
300        9.2972      12.4900      18.2186      11.8763      21.5798  ...   
350        1.3046       2.7611       9.1209       5.2616      16.6523  ...   
400           NaN       6.5449          NaN      15.6593       2.3958  ...   
450       12.6352       6.7424       0.5336      48.0796      29.7132  ...   
500       36.5891       2.5561      24.1121      57.4685      36.5633  ...   
550       67.3319       2.6181      56.1132      58.9974      38.1289  ...   
600       73.5402      11.3936      63.2800      79.6380      59.7698  ...   
650       70.9426      20.1378      61.2603      72.3035      50.3504  ...   
700       91.2316      41.4931      81.3250      53.6807      28.9866  ...   
750       92.7087      69.7966      82.3136      34.4050      13.0643  ...   
800       76.7883      74.0802      71.1310      29.2806       9.1215  ...   
850       55.6842      70.2796      48.8437      26.8481       7.3511  ...   
900       45.7854      87.5862      39.3280      25.5809       6.3492  ...   
950       44.0156      87.8584      37.8389      25.5024       6.4553  ...   
1000      43.7562      79.6518      37.5538      25.0612